# Classification Example

This code was from [a video Neil sent](https://www.youtube.com/watch?v=qWaEfgWi21o) demonstrating pixel-level classification using the US national landcover dataset. I ran through it (up until the export part) and modified the testing point to be in SE Asia. Leaving it here for reference with the geemap / ee libraries.

In [ ]:
# import ee
# import geemap
# ee.Authenticate()
# ee.Initialize(project='iuu-fishing-detections-asean')

In [ ]:
# All this is coming from the video Neil sent;
# https://www.youtube.com/watch?v=qWaEfgWi21o

# ee.ImageCollection('ESA/WorldCover/v200').first()
# ee.ImageCollection("COPERNICUS/S2").filterDate('2023-01-01', '2023-01-31')

In [ ]:
import ee
import geemap
ee.Authenticate()
ee.Initialize(project='iuu-fishing-detections-asean')

In [ ]:
Map = geemap.Map()
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

In [ ]:
# old point that's somewhere in Cali,
# point = ee.Geometry.Point([-122.4439, 37.7538])
# point = ee.Geometry.Point([-87.7719, 41.8799]) # this one was alr commented

# image = (
#     ee.ImageCollection("LANDSAT/LC08/C01/T1_SR")
#     .filterBounds(point)
#     .filterDate("2016-01-01", "2016-12-31")
#     .sort("CLOUD_COVER")
#     .first()
#     .select("B[1-7]")
# )

# vis_params = {"min": 0, "max": 3000, "bands": ["B4", "B3", "B2"]}

# Map.centerObject(point, 8)
# Map.addLayer(image, vis_params, "Landsat")

# new point that will be somewhere on a coast in ASEAN, used for testing
# Lat, lon -> 12.648179, 100.988062
# point = ee.Geometry.Point([100.988062, 12.648179])

# training point that's somewhere in Cali
point = ee.Geometry.Point([-122.4439, 37.7538])

image = (
    ee.ImageCollection("COPERNICUS/S2")
    .filterBounds(point)
    # .filterDate("2016-01-01", "2016-12-31") # this code here selects the
    .filterDate("2016-01-01", "2016-12-31")
    .sort("CLOUDY_PIXEL_PERCENTAGE")
    .first()
    .select("B[1-7]")
)

vis_params = {"min": 0, "max": 3000, "bands": ["B4", "B3", "B2"]}

Map.centerObject(point, 8)
Map.addLayer(image, vis_params, "Sentinel-2")

In [ ]:
# ee.Date(image.get("system:time_start")).format("YYYY-MM-dd").getInfo()
ee.Date(image.get("system:time_start")).getInfo()

{'type': 'Date', 'value': 1459883026456}

In [ ]:
image.get("CLOUDY_PIXEL_PERCENTAGE").getInfo()

0

In [ ]:
nlcd = ee.Image("USGS/NLCD/NLCD2016").select("landcover").clip(image.geometry())
Map.addLayer(nlcd, {}, "NLCD")
Map

Map(bottom=25636.0, center=[37.75379999999999, -122.44390000000001], controls=(WidgetControl(options=['positio…

In [ ]:
# Make the training dataset.
points = nlcd.sample(
    **{
        "region": image.geometry(),
        "scale": 30,
        "numPixels": 5000,
        "seed": 0,
        "geometries": True,  # Set this to False to ignore geometries
    }
)

Map.addLayer(points, {}, "training", False)

In [ ]:
print(points.size().getInfo())

3094


In [ ]:
print(points.first().getInfo())

{'type': 'Feature', 'geometry': {'type': 'Point', 'coordinates': [-122.17093717711913, 37.2761452194998]}, 'id': '0', 'properties': {'landcover': 43}}


In [ ]:
# Ideas to help make this more relevant to our project:
# # Use cloudcover layers in sentinel to mask out cloud-based false positives
# # Mess with which bands are used for training to see what gives better results
# # In the immediate moment, change the area to ASEAN waters

# # USE ee.geography.Point(coords, crs) TO TRANSLATE THE EPSG:____ COORDS INTO
# # ACTUAL COORDS

# # Also in the immediate moment, use the funny classifier to take US coast data
# # and predict landcover on ASEAN
# Done

# # Could try to do some classification that implements both the Sentinel and
# # Landsat data... actually idk how the time differences would work there.

# # Could try and implement austin's idea of averaging the GE images. With this
# # tutorial this shouldn't be that complicated in GEE... maybe

# # For realsies, this weekend I could try and make a file-scraper that creates
# # one aggregate file that contains all the boat locations, and gets all the
# # timestamps of the data in our files.

In [ ]:
# Use these bands for prediction.
bands = ["B1", "B2", "B3", "B4", "B5", "B6", "B7"]


# This property of the table stores the land cover labels.
label = "landcover"

# Overlay the points on the imagery to get training.
training = image.select(bands).sampleRegions(
    **{"collection": points, "properties": [label], "scale": 30}
)

# Train a CART classifier with default parameters.
trained = ee.Classifier.smileCart().train(training, label, bands)

In [ ]:
print(training.first().getInfo())

{'type': 'Feature', 'geometry': None, 'id': '0_0', 'properties': {'B1': 1014, 'B2': 762, 'B3': 652, 'B4': 417, 'B5': 772, 'B6': 1813, 'B7': 2358, 'landcover': 43}}


In [ ]:
# Classify the image with the same bands used for training.
result = image.select(bands).classify(trained)

# # Display the clusters with random colors.
Map.addLayer(result.randomVisualizer(), {}, "classified")
Map

Map(bottom=25636.0, center=[37.75379999999999, -122.44390000000001], controls=(WidgetControl(options=['positio…

In [ ]:
# new image for testing
asean_point = ee.Geometry.Point([100.988062, 12.648179])

asean_image = (
    ee.ImageCollection("COPERNICUS/S2")
    .filterBounds(asean_point)
    # .filterDate("2016-01-01", "2016-12-31") # this code here selects the
    .filterDate("2016-01-01", "2016-12-31")
    .sort("CLOUDY_PIXEL_PERCENTAGE")
    .first()
    .select("B[1-7]")
)

In [ ]:
asean_result = asean_image.select(bands).classify(trained)

# # Display the clusters with random colors.
Map.addLayer(asean_result.randomVisualizer(), {}, "asean_classified")
Map

Map(bottom=51058.0, center=[37.56635122499226, -122.09929063838099], controls=(WidgetControl(options=['positio…

In [ ]:
landcover = result.set("classification_class_values", class_values)
landcover = landcover.set("classification_class_palette", class_palette)

In [ ]:
Map.addLayer(landcover, {}, "Land cover")
Map

Map(bottom=25767.0, center=[37.182202221079805, -122.4149780615024], controls=(WidgetControl(options=['positio…

In [ ]:
print("Change layer opacity:")
cluster_layer = Map.layers[-1]
cluster_layer.interact(opacity=(0, 1, 0.1))

In [ ]:
Map.add_legend(builtin_legend="NLCD")
Map

In [ ]:
geemap.ee_export_image_to_drive(
    landcover, description="landcover", folder="classification_practice_export", scale=900
)

In [ ]:
class_palette = nlcd.get("landcover_class_palette").getInfo()
class_palette

['476ba1',
 'd1defa',
 'decaca',
 'd99482',
 'ee0000',
 'ab0000',
 'b3aea3',
 '68ab63',
 '1c6330',
 'b5ca8f',
 'a68c30',
 'ccba7d',
 'e3e3c2',
 'caca78',
 '99c247',
 '78ae94',
 'dcd93d',
 'ab7028',
 'bad9eb',
 '70a3ba']

In [ ]:
class_values = nlcd.get("landcover_class_values").getInfo()
class_values

[11,
 12,
 21,
 22,
 23,
 24,
 31,
 41,
 42,
 43,
 51,
 52,
 71,
 72,
 73,
 74,
 81,
 82,
 90,
 95]

# Actual Code

In [ ]:
# Okay from here on out its all me.

# Step 1: pull up literally any image from the dataset.
  # scrape for metadata file at data's root
  # pull the time, location, and crs from the file
  # create a new data point with the satellite, at given point with crs
  # scrape for featurecollection at  /layers/label/data.geojson
  # copy and paste onto the map

## Imports

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

data_dir = '/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/mikey'
small_data_dir = '/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack'

Mounted at /content/drive


In [ ]:
# For personal file scraping
import glob
from pathlib import Path
import json


In [ ]:
import ee
import geemap
ee.Authenticate()
ee.Initialize(project='iuu-fishing-detections-asean')

In [ ]:
pip install rasterio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.3/22.3 MB 54.7 MB/s eta 0:00:00


In [ ]:
# for coordinate translation
import rasterio
from rasterio.crs import CRS
from rasterio import warp

## First Image example

In [ ]:
# metadatas = {[{"ImageName": img.name, "time": json.load( open(str(img / "metadata.json")))['time_range'],
#       "bounds" : str(img / "layers/label/data.geojson"),
#       "crs" : len(json.load( open(str(img / "layers/label/data.geojson")))['features'])
#       # , "View": f'<img src="{img}" width="200" height="200">' # View is optional
#      } for img in Path(f"{small_data_dir}").glob("*")]}

# first_path = Path(f"{small_data_dir}").glob("*")

first_metadata = json.load( open(str(small_data_dir + "/1186117_1894101_158904" + "/metadata.json")))
first_img_name = open(str(small_data_dir + "/1186117_1894101_158904" + "/image_name_from_siv.txt")).read()[:-5]
# 1186117_1894101_158904

first_metadata
first_img_name
# first_img_id = first_img_name[11:27] + first_img_name[45:] + "_" + first_img_name[38:44]
# first_img_id

'20230603T154549_20230603T191134_T17QRU'

In [ ]:
# src_crs = CRS.from_string(first_metadata['projection']['crs'][:])
# dst_crs = CRS.from_epsg(4326)

# x,y = warp.transform(src_crs, dst_crs, [first_lon], [first_lat])
# print(x, y)
# reprojected_point = ee.Geometry.Point([x[0],y[0]])


[-85.48648052664744] [-1.7095448972698528]


CRS.from_epsg(32617)

In [175]:
first_rectangle_bounds = ee.Geometry.Rectangle(
    # [first_metadata['bounds'][0]*5, first_metadata['bounds'][3]*-5,
    #  first_metadata['bounds'][2]*5, first_metadata['bounds'][1]*-5],
    [first_metadata['bounds'][0], first_metadata['bounds'][1],
     first_metadata['bounds'][2], first_metadata['bounds'][3]],
    ee.Projection(first_metadata['projection']['crs'],
     [10, 0, 0, 0, -10, 0])
    , True, False
    )
first_rectangle_bounds.centroid()

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Geometry.centroid",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "GeometryConstructors.Rectangle",
          "arguments": {
            "coordinates": {
              "constantValue": [
                79843,
                -190013,
                80792,
                -189069
              ]
            },
            "crs": {
              "functionInvocationValue": {
                "functionName": "Projection",
                "arguments": {
                  "crs": {
                    "constantValue": "EPSG:32617"
                  },
                  "transform": {
                    "constantValue": [
                      10,
                      0,
                      0,
                      0,
                      -10,
                      0
                    ]
                  }
                }
              }
            },
            "evenOdd": {
              "constantValue": false
            },
            "geodesic": {
              "constantValue": true
            }
          }
        }
      }
    }
  }
})

In [167]:
first_dateRangeStart = ee.Date(first_metadata['time_range'][0])
first_dateRangeEnd = ee.Date(first_metadata['time_range'][1])


# 1st image id: COPERNICUS/S2_HARMONIZED/20230603T154549_20230603T154551_T17QRU
# PRODUCT_ID is the name of the field
#                                        20230603T154549_20230603T191134_T17QRU
# first_image = ee.Image("COPERNICUS/S2_HARMONIZED/20230603T154549_20230603T154551_T17QRU")

first_image = (
    ee.ImageCollection("COPERNICUS/S2_HARMONIZED")
    # .filterBounds(first_point)
    # .filterDate("2016-01-01", "2016-12-31") # this code here selects the
    .filterDate(first_dateRangeStart, first_dateRangeEnd)
    # .sort("CLOUDY_PIXEL_PERCENTAGE")
    # .first()
    .filter(ee.Filter.stringContains('PRODUCT_ID',first_img_name)) # 20230603T154549_20230603T191134_T17QRU
    # bands with spatial of 10 may be easier for now; b2-4, 8
    .select("B[2-4]", "B8")
    .first()
    .clip(first_rectangle_bounds)
)

first_image

In [170]:
# first_easting = (first_metadata['bounds'][2]+first_metadata['bounds'][0])*5
# first_northing = (first_metadata['bounds'][3]+first_metadata['bounds'][1])*-5
# first_point = ee.Geometry.Point([first_easting, first_northing]
#                        , first_metadata['projection']['crs']
#                        )

# first_easting = (first_metadata['bounds'][2]+first_metadata['bounds'][0])/2
# first_northing = (first_metadata['bounds'][3]+first_metadata['bounds'][1])/2
# first_point = ee.Geometry.Point(
#     [first_easting, first_northing]
#     , ee.Projection(first_metadata['projection']['crs'],
#      [10, 0, 0, 0, -10, 0])
#     )

first_point = first_rectangle_bounds.centroid()

first_point
# first_point.projection()


ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Geometry.centroid",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "GeometryConstructors.Rectangle",
          "arguments": {
            "coordinates": {
              "constantValue": [
                79843,
                -190013,
                80792,
                -189069
              ]
            },
            "crs": {
              "functionInvocationValue": {
                "functionName": "Projection",
                "arguments": {
                  "crs": {
                    "constantValue": "EPSG:32617"
                  },
                  "transform": {
                    "constantValue": [
                      10,
                      0,
                      0,
                      0,
                      -10,
                      0
                    ]
                  }
                }
              }
            },
            "evenOdd": {
              "constantValue": false
            },
            "geodesic": {
              "constantValue": true
            }
          }
        }
      }
    }
  }
})

In [174]:
Map = geemap.Map()

vis_params = {"min": 0, "max": 3000, "bands": ["B4", "B3", "B2"]}

Map.centerObject(first_point, 8)
Map.addLayer(first_image, vis_params, "Sentinel-2")
Map

Map(center=[17.123246812586803, -78.1508770163836], controls=(WidgetControl(options=['position', 'transparent_…

## Collective image example

In [ ]:
# from here I'm trying to create an image collection of all the test data
# ...and it works!!!

In [190]:
# image_collection = []
master_image = ee.ImageCollection([])

for img_folder in Path(f"{small_data_dir}").glob("*"):
  print(img_folder)
  metadata = json.load( open(str(img_folder / "metadata.json")))
  img_name = open(str(img_folder / "image_name_from_siv.txt")).read()[:-5]
  # would put lat/lon stuff here for labeled points... will get that soon
  # also here would create training non-vessel points for the unmarked pics
  # also also, need to clip image to bounds
  dateRangeStart = ee.Date(metadata['time_range'][0])
  dateRangeEnd = ee.Date(metadata['time_range'][1])

  rectangle_bounds = ee.Geometry.Rectangle(
    [metadata['bounds'][0], metadata['bounds'][1],
     metadata['bounds'][2], metadata['bounds'][3]],
    ee.Projection(metadata['projection']['crs'],
     [10, 0, 0, 0, -10, 0])
    , True, False
    )

  image = (
    ee.ImageCollection("COPERNICUS/S2_HARMONIZED")
    # .filterBounds(rectangle_bounds)
    .filterDate(dateRangeStart, dateRangeEnd)
    .filter(ee.Filter.stringContains('PRODUCT_ID',img_name))
    .select("B[2-4]", "B8")
    # TODO: need to add some extra checking here to make sure the above select
    #       doesn't return null. Specifically, 562176_... in the sample 7 is
    #       null even though a picture is in the dataset...
    # .first()
    # .clip(rectangle_bounds)
  )

  # image_collection.append(image)
  # if (image == Null):
  #   print("null img")
  Map.addLayer(image, vis_params, metadata['name'])
  master_image = master_image.merge(image)

# master_image = ee.ImageCollection(image_collection)
# Map.addLayer(master_image, vis_params, "combined images example")

master_image

/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/1186117_1894101_158904
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/464896_2199552_134025
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/542720_1308672_129570
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/562176_1317888_74483
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/978649_1780574_158735
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/562176_1317888_76285
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/561152_1314816_132052
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/304128_2197504_133255
/content/drive/MyDrive/Colab Notebooks/ASEAN_pics/sendtoslack/3875840_1474560_130468


In [189]:
Map = geemap.Map()

# Map.addLayer(master_image, vis_params, "Sentinel-2 test images")
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

## Collecting labels example

In [ ]:
second_metadata = json.load( open(str(small_data_dir + "/1186117_1894101_158904" + "/metadata.json")))
first_img_name = open(str(small_data_dir + "/1186117_1894101_158904" + "/image_name_from_siv.txt")).read()[:-5]
# 1186117_1894101_158904

first_metadata
first_img_name
# first_img_id = first_img_name[11:27] + first_img_name[45:] + "_" + first_img_name[38:44]
# first_img_id

'20230603T154549_20230603T191134_T17QRU'

In [ ]:
# src_crs = CRS.from_string(first_metadata['projection']['crs'][:])
# dst_crs = CRS.from_epsg(4326)

# x,y = warp.transform(src_crs, dst_crs, [first_lon], [first_lat])
# print(x, y)
# reprojected_point = ee.Geometry.Point([x[0],y[0]])


[-85.48648052664744] [-1.7095448972698528]


CRS.from_epsg(32617)

In [ ]:
first_dateRangeStart = ee.Date(first_metadata['time_range'][0])
first_dateRangeEnd = ee.Date(first_metadata['time_range'][1])


# 1st image id: COPERNICUS/S2_HARMONIZED/20230603T154549_20230603T154551_T17QRU
# PRODUCT_ID is the name of the field
#                                        20230603T154549_20230603T191134_T17QRU
# first_image = ee.Image("COPERNICUS/S2_HARMONIZED/20230603T154549_20230603T154551_T17QRU")

first_image = (
    ee.ImageCollection("COPERNICUS/S2_HARMONIZED")
    # .filterBounds(first_point)
    # .filterDate("2016-01-01", "2016-12-31") # this code here selects the
    .filterDate(first_dateRangeStart, first_dateRangeEnd)
    # .sort("CLOUDY_PIXEL_PERCENTAGE")
    # .first()
    .filter(ee.Filter.stringContains('PRODUCT_ID',first_img_name)) # 20230603T154549_20230603T191134_T17QRU
    # bands with spatial of 10 may be easier for now; b2-4, 8
    .select("B[2-4]", "B8")
)

first_image

In [ ]:
# first_easting = (first_metadata['bounds'][2]+first_metadata['bounds'][0])*5
# first_northing = (first_metadata['bounds'][3]+first_metadata['bounds'][1])*-5
# first_point = ee.Geometry.Point([first_easting, first_northing]
#                        , first_metadata['projection']['crs']
#                        )

first_easting = (first_metadata['bounds'][2]+first_metadata['bounds'][0])/2
first_northing = (first_metadata['bounds'][3]+first_metadata['bounds'][1])/2
first_point = ee.Geometry.Point(
    [first_easting, first_northing]
    , ee.Projection(first_metadata['projection']['crs'],
     [10, 0, 0, 0, -10, 0])
    )

first_point
# first_point.projection()


ee.Geometry({
  "functionInvocationValue": {
    "functionName": "GeometryConstructors.Point",
    "arguments": {
      "coordinates": {
        "constantValue": [
          80317.5,
          -189541.0
        ]
      },
      "crs": {
        "functionInvocationValue": {
          "functionName": "Projection",
          "arguments": {
            "crs": {
              "constantValue": "EPSG:32617"
            },
            "transform": {
              "constantValue": [
                10,
                0,
                0,
                0,
                -10,
                0
              ]
            }
          }
        }
      }
    }
  }
})

In [ ]:
Map = geemap.Map()

vis_params = {"min": 0, "max": 3000, "bands": ["B4", "B3", "B2"]}

Map.centerObject(first_point, 8)
Map.addLayer(first_image, vis_params, "Sentinel-2")
Map

Map(center=[17.12324694448032, -78.15087647996442], controls=(WidgetControl(options=['position', 'transparent_…